In [1]:
#libraries
from bs4 import BeautifulSoup
import pandas as pd
import numpy as np
import requests
import random
import time
import ipywidgets as widgets
from IPython.display import Javascript, display
from difflib import SequenceMatcher
import spotipy
from spotipy.oauth2 import SpotifyClientCredentials
import re

#credencials
spotify = spotipy.Spotify(client_credentials_manager=SpotifyClientCredentials(
        client_id='7b1cccc6a20546aa819d65942b6e98e3',
        client_secret='47a9a88346464b52823ade52b4be19af'))

In [2]:
selection = 'Pienso en aquella tarde'

In [3]:
results = spotify.search(selection, limit = 10)

In [4]:
results['tracks'].keys()

dict_keys(['href', 'items', 'limit', 'next', 'offset', 'previous', 'total'])

In [5]:
features = results['tracks']['items'][0]['uri']
features

'spotify:track:5dncXckT4fSDlyEL9QgzuY'

In [6]:
spotify.audio_features(features)

[{'danceability': 0.313,
  'energy': 0.869,
  'key': 7,
  'loudness': -4.206,
  'mode': 1,
  'speechiness': 0.0581,
  'acousticness': 0.0023,
  'instrumentalness': 0,
  'liveness': 0.47,
  'valence': 0.461,
  'tempo': 83.085,
  'type': 'audio_features',
  'id': '5dncXckT4fSDlyEL9QgzuY',
  'uri': 'spotify:track:5dncXckT4fSDlyEL9QgzuY',
  'track_href': 'https://api.spotify.com/v1/tracks/5dncXckT4fSDlyEL9QgzuY',
  'analysis_url': 'https://api.spotify.com/v1/audio-analysis/5dncXckT4fSDlyEL9QgzuY',
  'duration_ms': 172600,
  'time_signature': 4}]

In [7]:
#biggest data base
urls_los40 = []

years = list(range(1966,2020))

for year in years:
    urls_los40.append('https://los40.com/lista40/numeros1/'+str(year))


In [8]:
responses40 = []

for i in urls_los40:
    #make request
    response = requests.get(i)
    
    #store response
    responses40.append(response)
    print(response.status_code)
    
    #respectful nap:
    waiting_time = random.randint(1,3)
    print("I'm going to sleep for", waiting_time, "seconds")
    time.sleep(waiting_time)

200
I'm going to sleep for 2 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 2 seconds
200
I'm going to sleep for 2 seconds
200
I'm going to sleep for 1 seconds
200
I'm going to sleep for 2 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 1 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 2 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 1 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 1 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 2 seconds
200
I'm going to sleep for 1 seconds
200
I'm going to sleep for 2 seconds
200
I'm going to sleep for 1 seconds
200
I'm going to sleep for 2 seconds
200
I'm going to sleep for 1 seconds
200
I'm going to sleep for 3 seconds
200
I'm going to sleep for 2 seconds
2

In [9]:
all_responses = []

for response in responses40:
    all_responses.append(BeautifulSoup(response.content, 'html.parser'))
    
songs40 = []
artists40 = []

for each in all_responses:
    for song in each.select('div.info_grupo > p'):
        songs40.append (song.get_text())
    for artist in each.select('div.info_grupo > h4'):
        artists40.append(artist.get_text())


In [10]:
top_los40 = pd.DataFrame({
    "Song": songs40,
    "Artist":artists40,
})

In [14]:
top_los40.to_csv(r'Project')

In [15]:
playlists = spotify.user_playlist_tracks("spotify", 'https://open.spotify.com/playlist/1G8IpkZKobrIlXcVPoSIuf')

In [ ]:
playlists['items'][0]['track']['album']['artists'][0]['name']

In [18]:
ten_bands = []
ten_songs = []

for singer in playlists['items']:
    for singer1 in singer['track']['album']['artists']:
        ten_bands.append(singer1['name']) 

ten_bands

['Bob Dylan',
 'Nirvana',
 'The Beatles',
 'The Beach Boys',
 'The Rolling Stones',
 'Chuck Berry',
 'The Ronettes',
 'Marvin Gaye',
 'Marvin Gaye',
 'The Who',
 'Aretha Franklin',
 'Joy Division',
 'Bruce Springsteen',
 'The Rolling Stones',
 'Sex Pistols',
 'The Beatles',
 'Elvis Presley',
 'Michael Jackson',
 'The Clash',
 'The Beach Boys',
 'Led Zeppelin',
 'Otis Redding',
 'John Lennon',
 'Grandmaster Flash & The Furious Five',
 'Sex Pistols',
 'David Bowie',
 'OutKast',
 'The Kinks',
 'Prince',
 'Little Richard',
 'M.I.A.',
 'Jimi Hendrix',
 'The Rolling Stones',
 'Stevie Wonder',
 'Ray Charles & Friends',
 'The White Stripes',
 'Pulp',
 'New Order',
 'Queen',
 'Sam Cooke',
 'The Kingsmen',
 'The Beatles',
 'R.E.M.',
 'The Kinks',
 'The Doors',
 'Beyoncé',
 'The Jackson 5',
 'Led Zeppelin',
 'The Smiths',
 'Gnarls Barkley',
 'David Bowie',
 'Lou Reed',
 'Donna Summer',
 'The Byrds',
 'Franz Ferdinand',
 'The Rolling Stones',
 'Ike & Tina Turner',
 'Radiohead',
 'Beck',
 'The Righ

In [ ]:
playlists

In [19]:
def get_playlist_tracks(username,playlist_id):
    results = spotify.user_playlist_tracks(username,playlist_id)
    tracks = results['items']
    while results['next']:
        results = spotify.next(results)
        tracks.extend(results['items'])
    return tracks

In [20]:
entire_playlist = get_playlist_tracks('acclaimedmusic', 'https://open.spotify.com/playlist/1G8IpkZKobrIlXcVPoSIuf')

In [21]:
len(entire_playlist)

10000

In [22]:
entire_playlist

[{'added_at': '2018-07-15T21:44:28Z',
  'added_by': {'external_urls': {'spotify': 'https://open.spotify.com/user/acclaimedmusic'},
   'href': 'https://api.spotify.com/v1/users/acclaimedmusic',
   'id': 'acclaimedmusic',
   'type': 'user',
   'uri': 'spotify:user:acclaimedmusic'},
  'is_local': False,
  'primary_color': None,
  'track': {'album': {'album_type': 'album',
    'artists': [{'external_urls': {'spotify': 'https://open.spotify.com/artist/74ASZWbe4lXaubB36ztrGX'},
      'href': 'https://api.spotify.com/v1/artists/74ASZWbe4lXaubB36ztrGX',
      'id': '74ASZWbe4lXaubB36ztrGX',
      'name': 'Bob Dylan',
      'type': 'artist',
      'uri': 'spotify:artist:74ASZWbe4lXaubB36ztrGX'}],
    'available_markets': ['AD',
     'AE',
     'AL',
     'AR',
     'AT',
     'AU',
     'BA',
     'BE',
     'BG',
     'BH',
     'BO',
     'BR',
     'BY',
     'CA',
     'CH',
     'CL',
     'CO',
     'CR',
     'CY',
     'CZ',
     'DE',
     'DK',
     'DO',
     'DZ',
     'EC',
     'E

In [ ]:
entire_playlist[0]['track']['album']['artists'][0]['name']

In [23]:
ten_bands = []
ten_songs = []

for band in entire_playlist:
    for band1 in band['track']['album']['artists']:
        ten_bands.append(band1['name'])
    
len(ten_bands)

10118

In [24]:
artists10000 = []

for band in entire_playlist:
    for band1 in band['track']['album']['artists']:
        if len(band1['name'])<31:
            artists10000.append(band1['name'])
        
artists10000

['Bob Dylan',
 'Nirvana',
 'The Beatles',
 'The Beach Boys',
 'The Rolling Stones',
 'Chuck Berry',
 'The Ronettes',
 'Marvin Gaye',
 'Marvin Gaye',
 'The Who',
 'Aretha Franklin',
 'Joy Division',
 'Bruce Springsteen',
 'The Rolling Stones',
 'Sex Pistols',
 'The Beatles',
 'Elvis Presley',
 'Michael Jackson',
 'The Clash',
 'The Beach Boys',
 'Led Zeppelin',
 'Otis Redding',
 'John Lennon',
 'Sex Pistols',
 'David Bowie',
 'OutKast',
 'The Kinks',
 'Prince',
 'Little Richard',
 'M.I.A.',
 'Jimi Hendrix',
 'The Rolling Stones',
 'Stevie Wonder',
 'Ray Charles & Friends',
 'The White Stripes',
 'Pulp',
 'New Order',
 'Queen',
 'Sam Cooke',
 'The Kingsmen',
 'The Beatles',
 'R.E.M.',
 'The Kinks',
 'The Doors',
 'Beyoncé',
 'The Jackson 5',
 'Led Zeppelin',
 'The Smiths',
 'Gnarls Barkley',
 'David Bowie',
 'Lou Reed',
 'Donna Summer',
 'The Byrds',
 'Franz Ferdinand',
 'The Rolling Stones',
 'Ike & Tina Turner',
 'Radiohead',
 'Beck',
 'The Righteous Brothers',
 'The Crickets',
 'Ramon

In [ ]:
entire_playlist[0]['track']['name']

In [25]:
for song in entire_playlist:
    ten_songs.append(song['track']['name'])
    
ten_songs

['Like a Rolling Stone',
 'Smells Like Teen Spirit',
 'A Day In The Life - Remastered',
 'Good Vibrations (Mono)',
 "(I Can't Get No) Satisfaction - Mono Version / Remastered 2002",
 'Johnny B Goode',
 'Be My Baby',
 'I Heard It Through The Grapevine',
 "What's Going On",
 'My Generation - Original Mono Version',
 'Respect',
 'Love Will Tear Us Apart',
 'Born to Run',
 'Sympathy For The Devil',
 'Anarchy In The UK - Remastered 2012',
 'Strawberry Fields Forever - Remastered',
 'Heartbreak Hotel',
 'Billie Jean',
 'London Calling',
 'God Only Knows - Remastered',
 'Stairway To Heaven',
 "(Sittin' On) the Dock of the Bay",
 'Imagine - Remastered 2010',
 'The Message (feat. Melle Mel & Duke Bootee)',
 'God Save The Queen',
 'Heroes - 1999 Remaster',
 'Hey Ya! - Radio Mix / Club Mix',
 'You Really Got Me',
 'When Doves Cry',
 'Tutti Frutti',
 'Paper Planes',
 'Purple Haze',
 'Gimme Shelter',
 'Superstition',
 "What'd I Say",
 'Seven Nation Army',
 'Common People',
 'Blue Monday',
 'Bohemia

In [26]:
print(len(ten_songs))
print(len(ten_bands))

10000
10118


In [ ]:
ten_bands[-1]

In [27]:
top_10000 = pd.DataFrame({
    "Song": ten_songs,
    "Artist": artists10000,
})

In [28]:
top_10000

Song              Artist
0                                  Like a Rolling Stone           Bob Dylan
1                               Smells Like Teen Spirit             Nirvana
2                        A Day In The Life - Remastered         The Beatles
3                                Good Vibrations (Mono)      The Beach Boys
4     (I Can't Get No) Satisfaction - Mono Version /...  The Rolling Stones
...                                                 ...                 ...
9995                                 Here It Goes Again               OK Go
9996                      Be Quiet and Drive (Far Away)            Deftones
9997                                That Is Rock’n’Roll        The Coasters
9998                                        She Cracked   The Modern Lovers
9999                                      I Need A Sign     Badly Drawn Boy

[10000 rows x 2 columns]

In [33]:
frames = [top_10000, top_los40]

In [35]:
all_songs = pd.concat(frames)

In [36]:
all_songs.to_csv('allsongs.csv')